# Determinación de la Curva ROC y el Cut off

* Kernel Python 3.09.12

In [11]:
#!/usr/bin/env python
#-*- coding: utf-8 -*-

# ! pip install --upgrade pip
# !pip install --upgrade scikit-learn
# !pip install --upgrade pandas
# !pip install --upgrade matplotlib
# !pip install --upgrade seaborn
# !pip install --upgrade scipy
# ! pip install session-info --upgrade
# !pip install --upgrade numpy 
# !pip install plotly --upgrade
# !pip install chart-studio --upgrade
# !pip install ibm-cos-sdk #Documentación: https://ibm.github.io/ibm-cos-sdk-python/
# !pip install boto3

In [12]:
# Instalamos las librerias necesarias
# import chart_studio.plotly as py
import plotly.graph_objs as go
import plotly as plotly
import pandas as pd
from botocore.client import Config
import numpy as np
# import numpy.dual as dual --> Deprecado
import scipy as sp
from sklearn import metrics
import types
import pandas as pd
from botocore.client import Config
import ibm_boto3 #Documentación: https://ibm.github.io/ibm-cos-sdk-python/
def __iter__(self): return 0

# Librería de advertencias
import warnings
warnings.filterwarnings("ignore")

import session_info

session_info.show()
#Un-Comment these options if you want to exapand the number of rows and columns of you see visually in the notebook.
#pd.set_option('display.max_columns', None)
#pd.set_option('display.max_rows', None)


# Articulo

* Link: https://medium.com/swlh/determining-a-cut-off-or-threshold-when-working-with-a-binary-dependent-target-variable-7c2342cf2a7c

In [13]:
# Cargamos el dataset
pd_data = pd.read_csv("https://raw.githubusercontent.com/Franciscoletelier/Python-Projects/master/Determining%20ROC%20Curve/df_for_export-2.csv", sep=",", header=0)
pd_data.sample(10)

ID     DATE  FAILURE_TARGET    P_FAIL
37239   100151  8/13/15               0  0.048254
82712   100307  1/14/16               0  0.088303
126853  100457   3/4/15               0  0.585486
53636   100218   9/4/16               0  0.205745
53657   100218  6/27/16               0  0.147652
153666  100571  2/11/16               0  0.362022
18339   100081  5/12/16               0  0.092681
85549   100314  4/16/16               0  0.518397
115044  100413  6/29/16               0  0.401010
135669  100492  5/10/15               0  0.255385

## 3.0 Introducing a Gains Table

### 3.1 Assign Deciles based on the probability

In [14]:
dfx= pd.DataFrame(pd_data)
dfx.head()

ID     DATE  FAILURE_TARGET    P_FAIL
0  100003   4/5/16               0  0.177485
1  100003  3/30/16               0  0.208043
2  100003  3/31/16               0  0.194013
3  100003   4/1/16               0  0.158498
4  100003   4/2/16               0  0.190317

In [15]:
#Sort the data by ID and Date
dfx=dfx.sort_values(by=['P_FAIL'], ascending=False)

In [16]:
#add a very small random number to the probability to break ties
dfx['wookie'] = (np.random.randint(0, 100, dfx.shape[0]))/100000000000000000
dfx['P_FAIL']=dfx['P_FAIL']+dfx['wookie']
#Create deciles based on P_FAIL
dfx['DECILE'] = pd.qcut(dfx['P_FAIL'], 10, labels=np.arange(100, 0, -10))

### 3.2 Assemble the Gains Table

In [17]:
# Find the minimum probability for each decile
tips_summedv = pd.DataFrame(dfx.groupby(['DECILE'])['P_FAIL'].min())
# Find the maximum probability of each decile
tips_summedw = pd.DataFrame(dfx.groupby(['DECILE'])['P_FAIL'].max())
# Find the Actual Failure rate for each decile.
tips_summedx = pd.DataFrame(dfx.groupby(['DECILE'])['FAILURE_TARGET'].mean())
#Sum the number of Failures in each decile.
tips_summedy = pd.DataFrame(dfx.groupby(['DECILE'])['FAILURE_TARGET'].sum())
# count the records in each decile
tips_summedz = pd.DataFrame(dfx.groupby(['DECILE'])['FAILURE_TARGET'].count())


In [18]:
#Aggregate the summaries into one dataframe
tips = pd.concat([tips_summedv,tips_summedw, tips_summedx, tips_summedy,tips_summedz], axis=1)
tips.columns = ['MIN_SCORE','MAX_SCORE','FAILURE_RATE','FAILURES', 'OBS']


In [20]:
tips=tips.sort_values(by=['DECILE'], ascending=[False])
gains=tips
#Find the number of cumulative failures by decile.
gains['CUML_FAILURES']=gains['FAILURES'].cumsum()
#Find the percentage of failures in each decile
gains['PCT_OF_FAILURES']=(gains.FAILURES)/(dfx['FAILURE_TARGET'].sum())*100
#Find the cumulative percentage of failures in each decile.
gains['CUML_PCT_OF_FAILURES']=gains.PCT_OF_FAILURES.cumsum()
#Format the final output
gains=gains[['OBS','MIN_SCORE','MAX_SCORE','FAILURES','FAILURE_RATE','PCT_OF_FAILURES','CUML_FAILURES','CUML_PCT_OF_FAILURES']]
gains

OBS  MIN_SCORE  MAX_SCORE  FAILURES  FAILURE_RATE  PCT_OF_FAILURES  \
DECILE                                                                         
10      16521   0.634321   0.975795      3265      0.197627        69.959289   
20      16520   0.455667   0.634312       818      0.049516        17.527319   
30      16521   0.335289   0.455661       354      0.021427         7.585172   
40      16520   0.252277   0.335284       143      0.008656         3.064067   
50      16521   0.191109   0.252276        62      0.003753         1.328477   
60      16520   0.146307   0.191104        20      0.001211         0.428541   
70      16521   0.111849   0.146306         3      0.000182         0.064281   
80      16520   0.080237   0.111848         2      0.000121         0.042854   
90      16521   0.041927   0.080236         0      0.000000         0.000000   
100     16521   0.001404   0.041925         0      0.000000         0.000000   

        CUML_FAILURES  CUML_PCT_OF_FAILURES  
DECILE                                       
10               3265             69.959289  
20               4083             87.486608  
30               4437             95.071781  
40               4580             98.135847  
50               4642             99.464324  
60               4662             99.892865  
70               4665             99.957146  
80               4667            100.000000  
90               4667            100.000000  
100              4667            100.000000

## 4.0 Finding the best cut-off

### 4.1 Morphing a Gains Table into a continuum of cut-offs

In [21]:
dfx=pd_data
#Add a small negative random number to P_FAIL to break ties when grouping
dfx['wookie'] = (np.random.randint(0, 100, dfx.shape[0]))/100000000000000000
dfx['P_FAIL']=dfx['P_FAIL']+dfx['wookie']

# Instead of deciles, we create 10000 groups, based on the probability to fail.

In [22]:
dfx['GROUPS'] = pd.qcut(dfx['P_FAIL'], 10000, labels=False)
# find the minimum P_FAIL for each group.  This is a potential cut-off point.
tips_summedb = pd.DataFrame(dfx.groupby(['GROUPS'])['P_FAIL'].min())
#Find the number of Failures in each group
tips_summedz = pd.DataFrame(dfx.groupby(['GROUPS'])['FAILURE_TARGET'].sum())
#find the number of observations in each group
tips_summeda = pd.DataFrame(dfx.groupby(['GROUPS'])['FAILURE_TARGET'].count())
#append the summaries into one dataframe
tips = pd.concat([tips_summedb,tips_summedz, tips_summeda], axis=1)
tips.columns = ['CUT-OFF','FAILURES', 'OBS']
#find the number of non-failures
tips['NON_FAILURES']=tips.OBS-tips.FAILURES
#reset the index to make GROUPS a column
tips.reset_index(level=0, inplace=True)
#sort the dataframe by groups in descending order
tips=tips.sort_values(by=['GROUPS'], ascending=[False])
# Cumulative sum the failures, non-failures and observations
tips['INV_CUM_FAILURES'] = tips.FAILURES.cumsum()
tips['INV_CUM_NON_FAILURES'] = tips.NON_FAILURES.cumsum()
tips['TOTAL_OBS']=tips.OBS.sum()
#Sort the data by Groups ascending
tips=tips.sort_values(by=['GROUPS'], ascending=[True])
#calculate the total number of failures and non-failures
tips['CUM_FAILURES'] = tips.FAILURES.cumsum()
tips['CUM_NON_FAILURES'] = tips.NON_FAILURES.cumsum()
#find the total number of failures for the whole dataset.
tips['TOTAL_FAILURES']=tips.FAILURES.sum()
tips['TOTAL_NON_FAILURES']=tips.NON_FAILURES.sum()
#define the true positives for each cut-off
tips['TRUE_POSITIVES']=tips.INV_CUM_FAILURES
#define the false positives for each cut-off
tips['FALSE_POSITIVES']=tips.INV_CUM_NON_FAILURES
#define the true negatives for each cut-off
tips['TRUE_NEGATIVES']=tips.CUM_NON_FAILURES-tips.NON_FAILURES
#define the false negatives for each cut-off
tips['FALSE_NEGATIVES']=tips.CUM_FAILURES-tips.FAILURES
#double check the logic and arithmetic.
tips['OBS2']=tips.TRUE_POSITIVES+tips.FALSE_POSITIVES+tips.TRUE_NEGATIVES+tips.FALSE_NEGATIVES
# define the sensitvity for each cut-off
tips['SENSITIVITY']=tips['TRUE_POSITIVES']/(tips['TRUE_POSITIVES']+tips['FALSE_NEGATIVES'])
#define the specificity for each cut-off
tips['SPECIFICITY']=tips['TRUE_NEGATIVES']/(tips['FALSE_POSITIVES']+tips['TRUE_NEGATIVES'])
#define the false positive rate for each cut-off
tips['FALSE_POSITIVE_RATE']=1-tips['SPECIFICITY']
#define the false negative rate for each cut-off
tips['FALSE_NEGATIVE_RATE']=1-tips['SENSITIVITY']
tipsx=tips
gains=tipsx[['GROUPS','CUT-OFF','TRUE_POSITIVES','FALSE_POSITIVES','TRUE_NEGATIVES','FALSE_NEGATIVES','SENSITIVITY',
            'SPECIFICITY','FALSE_POSITIVE_RATE','FALSE_NEGATIVE_RATE']]
gains

GROUPS   CUT-OFF  TRUE_POSITIVES  FALSE_POSITIVES  TRUE_NEGATIVES  \
0          0  0.001404            4667           160539               0   
1          1  0.002718            4667           160522              17   
2          2  0.003173            4667           160505              34   
3          3  0.003342            4667           160489              50   
4          4  0.003520            4667           160472              67   
...      ...       ...             ...              ...             ...   
9995    9995  0.958857              71               12          160527   
9996    9996  0.959056              53               12          160527   
9997    9997  0.961913              43                7          160532   
9998    9998  0.963536              32                1          160538   
9999    9999  0.966488              17                0          160539   

      FALSE_NEGATIVES  SENSITIVITY  SPECIFICITY  FALSE_POSITIVE_RATE  \
0                   0     1.000000     0.000000             1.000000   
1                   0     1.000000     0.000106             0.999894   
2                   0     1.000000     0.000212             0.999788   
3                   0     1.000000     0.000311             0.999689   
4                   0     1.000000     0.000417             0.999583   
...               ...          ...          ...                  ...   
9995             4596     0.015213     0.999925             0.000075   
9996             4614     0.011356     0.999925             0.000075   
9997             4624     0.009214     0.999956             0.000044   
9998             4635     0.006857     0.999994             0.000006   
9999             4650     0.003643     1.000000             0.000000   

      FALSE_NEGATIVE_RATE  
0                0.000000  
1                0.000000  
2                0.000000  
3                0.000000  
4                0.000000  
...                   ...  
9995             0.984787  
9996             0.988644  
9997             0.990786  
9998             0.993143  
9999             0.996357  

[10000 rows x 10 columns]

### 4.2 Finding the cut-off with the smallest misclassification rate

In [23]:
tips=tipsx
#sum the false positives and false negatives.
tips['FALSE_CLASSIFICATIONS'] = tips.FALSE_POSITIVES+tips.FALSE_NEGATIVES
#estimate the false classification rate
tips['FALSE_CLASSIFICATION_RATE']=tips.FALSE_CLASSIFICATIONS/(tips.TOTAL_OBS)
gains=tips[['GROUPS','CUT-OFF','TRUE_POSITIVES','FALSE_POSITIVES','TRUE_NEGATIVES','FALSE_NEGATIVES','SENSITIVITY',
            'SPECIFICITY','FALSE_POSITIVE_RATE','FALSE_NEGATIVE_RATE','FALSE_CLASSIFICATIONS','FALSE_CLASSIFICATION_RATE']]
gains

GROUPS   CUT-OFF  TRUE_POSITIVES  FALSE_POSITIVES  TRUE_NEGATIVES  \
0          0  0.001404            4667           160539               0   
1          1  0.002718            4667           160522              17   
2          2  0.003173            4667           160505              34   
3          3  0.003342            4667           160489              50   
4          4  0.003520            4667           160472              67   
...      ...       ...             ...              ...             ...   
9995    9995  0.958857              71               12          160527   
9996    9996  0.959056              53               12          160527   
9997    9997  0.961913              43                7          160532   
9998    9998  0.963536              32                1          160538   
9999    9999  0.966488              17                0          160539   

      FALSE_NEGATIVES  SENSITIVITY  SPECIFICITY  FALSE_POSITIVE_RATE  \
0                   0     1.000000     0.000000             1.000000   
1                   0     1.000000     0.000106             0.999894   
2                   0     1.000000     0.000212             0.999788   
3                   0     1.000000     0.000311             0.999689   
4                   0     1.000000     0.000417             0.999583   
...               ...          ...          ...                  ...   
9995             4596     0.015213     0.999925             0.000075   
9996             4614     0.011356     0.999925             0.000075   
9997             4624     0.009214     0.999956             0.000044   
9998             4635     0.006857     0.999994             0.000006   
9999             4650     0.003643     1.000000             0.000000   

      FALSE_NEGATIVE_RATE  FALSE_CLASSIFICATIONS  FALSE_CLASSIFICATION_RATE  
0                0.000000                 160539                   0.971750  
1                0.000000                 160522                   0.971648  
2                0.000000                 160505                   0.971545  
3                0.000000                 160489                   0.971448  
4                0.000000                 160472                   0.971345  
...                   ...                    ...                        ...  
9995             0.984787                   4608                   0.027892  
9996             0.988644                   4626                   0.028001  
9997             0.990786                   4631                   0.028032  
9998             0.993143                   4636                   0.028062  
9999             0.996357                   4650                   0.028147  

[10000 rows x 12 columns]

In [24]:
x1 = tips['CUT-OFF']
y1 = tips['FALSE_POSITIVE_RATE']
y2 = tips['FALSE_NEGATIVE_RATE']
y3 = tips['FALSE_CLASSIFICATION_RATE']
trace = go.Scatter(
    x = x1,
    y = y1,
    name='False Positive Rate')
trace2 = go.Scatter(
    x = x1,
    y = y2,
    name='False Negative Rate'
)
trace3 = go.Scatter(
    x = x1,
    y = y3,
    name='False Classification Rate'
)
layout = go.Layout(
    title='Mis-Classification Rates BY CUT OFF SCORE',
    xaxis=dict(
        title='CUT OFF SCORE',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='False Positive and False Negative Rates',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    showlegend=True,
)
    
data=[trace,trace2,trace3]  
fig = go.Figure(data=data, layout=layout)
#plot_url = py.plot(fig, filename='styling-names')
plotly.offline.iplot(fig, filename='shapes-lines')

In [25]:
gains=gains.sort_values(by=['FALSE_CLASSIFICATION_RATE'], ascending=[True])
gains=gains.head(1)
gains

GROUPS   CUT-OFF  TRUE_POSITIVES  FALSE_POSITIVES  TRUE_NEGATIVES  \
9937    9937  0.909427             685              356          160183   

      FALSE_NEGATIVES  SENSITIVITY  SPECIFICITY  FALSE_POSITIVE_RATE  \
9937             3982     0.146775     0.997782             0.002218   

      FALSE_NEGATIVE_RATE  FALSE_CLASSIFICATIONS  FALSE_CLASSIFICATION_RATE  
9937             0.853225                   4338                   0.026258

In [30]:
# dfx=pd_data
dfx['Y_FAIL'] = np.where(((dfx.P_FAIL <= .909427)), 0, 1).astype(float)
print(pd.crosstab(dfx.Y_FAIL, dfx.FAILURE_TARGET, dropna=False))
pd.crosstab(dfx.Y_FAIL, dfx.FAILURE_TARGET).apply(lambda r: r/r.sum(), axis=1)

FAILURE_TARGET       0     1
Y_FAIL                      
0.0             160183  3982
1.0                356   685


FAILURE_TARGET         0         1
Y_FAIL                            
0.0             0.975744  0.024256
1.0             0.341979  0.658021

In [31]:
x2 = tips['CUT-OFF']
x1 = tips['FALSE_POSITIVE_RATE']
y1 = tips['SENSITIVITY']
trace = go.Scatter(
    x = x1,
    y = y1,
    name='ROC')
trace2 = go.Scatter(
    x = x2,
    y = y1,
    name='Cut-Off v TPR'
)
layout = go.Layout(
    title='ROC with Threshold Levels',
    xaxis=dict(
        title='False Positive Rate and Threshold Level',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='True Positive Rate',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    showlegend=True,
)
    
data=[trace,trace2]  
fig = go.Figure(data=data, layout=layout)
#plot_url = py.plot(fig, filename='styling-names')
plotly.offline.iplot(fig, filename='shapes-lines')

## 4.3 Finding the cut-off when the costs of false positives and false negatives are not equal

In [32]:
#define the cost of a false positive and false negative
cost_of_a_false_positive=1
cost_of_a_false_negative=2
#convert the costs into weights that sum to one
fp_weight=(cost_of_a_false_positive)/(cost_of_a_false_positive+cost_of_a_false_negative)
fn_weight=(cost_of_a_false_negative)/(cost_of_a_false_positive+cost_of_a_false_negative)
#Create a weighted false classification rate based on the costs of a false positive and a false negative.
tips['FALSE_CLASSIFICATIONS_W'] = np.where(((2*(((fp_weight)*tips.FALSE_POSITIVES+(fn_weight)*tips.FALSE_NEGATIVES)) >= tips.TOTAL_OBS)), tips.TOTAL_OBS, 2*(((fp_weight)*tips.FALSE_POSITIVES+(fn_weight)*tips.FALSE_NEGATIVES)))
tips['FALSE_CLASSIFICATION_RATE_W']=tips.FALSE_CLASSIFICATIONS_W/(tips.TOTAL_OBS)
gains=tips[['GROUPS','CUT-OFF','TRUE_POSITIVES','FALSE_POSITIVES','TRUE_NEGATIVES','FALSE_NEGATIVES','SENSITIVITY',
            'SPECIFICITY','FALSE_POSITIVE_RATE','FALSE_NEGATIVE_RATE','FALSE_CLASSIFICATIONS_W','FALSE_CLASSIFICATION_RATE_W']]
gains

GROUPS   CUT-OFF  TRUE_POSITIVES  FALSE_POSITIVES  TRUE_NEGATIVES  \
0          0  0.001404            4667           160539               0   
1          1  0.002718            4667           160522              17   
2          2  0.003173            4667           160505              34   
3          3  0.003342            4667           160489              50   
4          4  0.003520            4667           160472              67   
...      ...       ...             ...              ...             ...   
9995    9995  0.958857              71               12          160527   
9996    9996  0.959056              53               12          160527   
9997    9997  0.961913              43                7          160532   
9998    9998  0.963536              32                1          160538   
9999    9999  0.966488              17                0          160539   

      FALSE_NEGATIVES  SENSITIVITY  SPECIFICITY  FALSE_POSITIVE_RATE  \
0                   0     1.000000     0.000000             1.000000   
1                   0     1.000000     0.000106             0.999894   
2                   0     1.000000     0.000212             0.999788   
3                   0     1.000000     0.000311             0.999689   
4                   0     1.000000     0.000417             0.999583   
...               ...          ...          ...                  ...   
9995             4596     0.015213     0.999925             0.000075   
9996             4614     0.011356     0.999925             0.000075   
9997             4624     0.009214     0.999956             0.000044   
9998             4635     0.006857     0.999994             0.000006   
9999             4650     0.003643     1.000000             0.000000   

      FALSE_NEGATIVE_RATE  FALSE_CLASSIFICATIONS_W  \
0                0.000000            107026.000000   
1                0.000000            107014.666667   
2                0.000000            107003.333333   
3                0.000000            106992.666667   
4                0.000000            106981.333333   
...                   ...                      ...   
9995             0.984787              6136.000000   
9996             0.988644              6160.000000   
9997             0.990786              6170.000000   
9998             0.993143              6180.666667   
9999             0.996357              6200.000000   

      FALSE_CLASSIFICATION_RATE_W  
0                        0.647834  
1                        0.647765  
2                        0.647696  
3                        0.647632  
4                        0.647563  
...                           ...  
9995                     0.037142  
9996                     0.037287  
9997                     0.037347  
9998                     0.037412  
9999                     0.037529  

[10000 rows x 12 columns]

In [33]:
x1 = tips['CUT-OFF']
y1 = tips['FALSE_POSITIVE_RATE']
y2 = tips['FALSE_NEGATIVE_RATE']
y3 = tips['FALSE_CLASSIFICATION_RATE_W']
trace = go.Scatter(
    x = x1,
    y = y1,
    name='False Positive Rate')
trace2 = go.Scatter(
    x = x1,
    y = y2,
    name='False Negative Rate'
)
trace3 = go.Scatter(
    x = x1,
    y = y3,
    name='Weighted False Classification Rate'
)
layout = go.Layout(
    title='Weighted Mis-Classification Rates BY CUT OFF SCORE',
    xaxis=dict(
        title='CUT OFF SCORE',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='Weighted False Positive and False Negative Rates',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    showlegend=True,
)
    
data=[trace,trace2,trace3]  
fig = go.Figure(data=data, layout=layout)
#plot_url = py.plot(fig, filename='styling-names')
plotly.offline.iplot(fig, filename='shapes-lines')

In [34]:
gains=gains.sort_values(by=['FALSE_CLASSIFICATION_RATE_W'], ascending=[True])
gains=gains.head(1)
gains

GROUPS   CUT-OFF  TRUE_POSITIVES  FALSE_POSITIVES  TRUE_NEGATIVES  \
9877    9877  0.882466            1102              928          159611   

      FALSE_NEGATIVES  SENSITIVITY  SPECIFICITY  FALSE_POSITIVE_RATE  \
9877             3565     0.236126     0.994219             0.005781   

      FALSE_NEGATIVE_RATE  FALSE_CLASSIFICATIONS_W  \
9877             0.763874                   5372.0   

      FALSE_CLASSIFICATION_RATE_W  
9877                     0.032517

In [35]:
dfx['Y_FAIL'] = np.where(((dfx.P_FAIL <= .8802)), 0, 1)
print(pd.crosstab(dfx.Y_FAIL, dfx.FAILURE_TARGET, dropna=False))
pd.crosstab(dfx.Y_FAIL, dfx.FAILURE_TARGET).apply(lambda r: r/r.sum(), axis=1)

FAILURE_TARGET       0     1
Y_FAIL                      
0               159543  3531
1                  996  1136


FAILURE_TARGET         0         1
Y_FAIL                            
0               0.978347  0.021653
1               0.467167  0.532833

## 4.4 Finding a cut-off when the economic costs are known.

In [36]:
#Define the False Positive and False Negative Weights.
cost_of_a_false_positive=2500
cost_of_a_false_negative=27500
fp_weight=(cost_of_a_false_positive)/(cost_of_a_false_positive+cost_of_a_false_negative)
fn_weight=(cost_of_a_false_negative)/(cost_of_a_false_positive+cost_of_a_false_negative)
#Define the False Classification Rate
tips['FALSE_CLASSIFICATIONS_W'] = np.where(((2*(((fp_weight)*tips.FALSE_POSITIVES+(fn_weight)*tips.FALSE_NEGATIVES)) >= tips.TOTAL_OBS)), tips.TOTAL_OBS, 2*(((fp_weight)*tips.FALSE_POSITIVES+(fn_weight)*tips.FALSE_NEGATIVES)))
tips['FALSE_CLASSIFICATION_RATE_W']=tips.FALSE_CLASSIFICATIONS_W/(tips.TOTAL_OBS)
tips['TOTAL_COST']=tips.FALSE_POSITIVES*cost_of_a_false_positive+tips.FALSE_NEGATIVES*cost_of_a_false_negative
gains=tips[['GROUPS','CUT-OFF','TRUE_POSITIVES','FALSE_POSITIVES','TRUE_NEGATIVES','FALSE_NEGATIVES','SENSITIVITY',
            'SPECIFICITY','FALSE_POSITIVE_RATE','FALSE_NEGATIVE_RATE','FALSE_CLASSIFICATIONS_W','FALSE_CLASSIFICATION_RATE_W','TOTAL_COST']]
gains

GROUPS   CUT-OFF  TRUE_POSITIVES  FALSE_POSITIVES  TRUE_NEGATIVES  \
0          0  0.001404            4667           160539               0   
1          1  0.002718            4667           160522              17   
2          2  0.003173            4667           160505              34   
3          3  0.003342            4667           160489              50   
4          4  0.003520            4667           160472              67   
...      ...       ...             ...              ...             ...   
9995    9995  0.958857              71               12          160527   
9996    9996  0.959056              53               12          160527   
9997    9997  0.961913              43                7          160532   
9998    9998  0.963536              32                1          160538   
9999    9999  0.966488              17                0          160539   

      FALSE_NEGATIVES  SENSITIVITY  SPECIFICITY  FALSE_POSITIVE_RATE  \
0                   0     1.000000     0.000000             1.000000   
1                   0     1.000000     0.000106             0.999894   
2                   0     1.000000     0.000212             0.999788   
3                   0     1.000000     0.000311             0.999689   
4                   0     1.000000     0.000417             0.999583   
...               ...          ...          ...                  ...   
9995             4596     0.015213     0.999925             0.000075   
9996             4614     0.011356     0.999925             0.000075   
9997             4624     0.009214     0.999956             0.000044   
9998             4635     0.006857     0.999994             0.000006   
9999             4650     0.003643     1.000000             0.000000   

      FALSE_NEGATIVE_RATE  FALSE_CLASSIFICATIONS_W  \
0                0.000000             26756.500000   
1                0.000000             26753.666667   
2                0.000000             26750.833333   
3                0.000000             26748.166667   
4                0.000000             26745.333333   
...                   ...                      ...   
9995             0.984787              8428.000000   
9996             0.988644              8461.000000   
9997             0.990786              8478.500000   
9998             0.993143              8497.666667   
9999             0.996357              8525.000000   

      FALSE_CLASSIFICATION_RATE_W  TOTAL_COST  
0                        0.161958   401347500  
1                        0.161941   401305000  
2                        0.161924   401262500  
3                        0.161908   401222500  
4                        0.161891   401180000  
...                           ...         ...  
9995                     0.051015   126420000  
9996                     0.051215   126915000  
9997                     0.051321   127177500  
9998                     0.051437   127465000  
9999                     0.051602   127875000  

[10000 rows x 13 columns]

In [37]:
x1 = tips['CUT-OFF']
y1 = tips['FALSE_POSITIVE_RATE']
y2 = tips['FALSE_NEGATIVE_RATE']
y3 = tips['FALSE_CLASSIFICATION_RATE_W']
trace = go.Scatter(
    x = x1,
    y = y1,
    name='False Positive Rate')
trace2 = go.Scatter(
    x = x1,
    y = y2,
    name='False Negative Rate'
)
trace3 = go.Scatter(
    x = x1,
    y = y3,
    name='Weighted False Classification Rate'
)
layout = go.Layout(
    title='Weighted Mis-Classification Rates BY CUT OFF SCORE',
    xaxis=dict(
        title='CUT OFF SCORE',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='False Positive and False Negative Rates',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    showlegend=True,
)
    
data=[trace,trace2,trace3]  
fig = go.Figure(data=data, layout=layout)
#plot_url = py.plot(fig, filename='styling-names')
plotly.offline.iplot(fig, filename='shapes-lines')

#### Let’s examine the relationship between Total Costs and the cut-off or threshold level

In [38]:
x1 = tips['CUT-OFF']
y1 = tips['TOTAL_COST']
trace = go.Scatter(
    x = x1,
    y = y1,
    name='Total Cost')
layout = go.Layout(
    title='Cut-Off Levels and Total Cost',
    xaxis=dict(
        title='CUT OFF SCORE',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    yaxis=dict(
        title='Total Costs',
        titlefont=dict(
            family='Courier New, monospace',
            size=18,
            color='#7f7f7f'
        )
    ),
    showlegend=True,
)
    
data=[trace]  
fig = go.Figure(data=data, layout=layout)
#plot_url = py.plot(fig, filename='styling-names')
plotly.offline.iplot(fig, filename='shapes-lines')

In [40]:
gains=gains.sort_values(by=['TOTAL_COST'], ascending=True)
gains=gains.head(1)
gains

GROUPS   CUT-OFF  TRUE_POSITIVES  FALSE_POSITIVES  TRUE_NEGATIVES  \
9135    9135  0.665541            3102            11189          149350   

      FALSE_NEGATIVES  SENSITIVITY  SPECIFICITY  FALSE_POSITIVE_RATE  \
9135             1565     0.664667     0.930304             0.069696   

      FALSE_NEGATIVE_RATE  FALSE_CLASSIFICATIONS_W  \
9135             0.335333                   4734.0   

      FALSE_CLASSIFICATION_RATE_W  TOTAL_COST  
9135                     0.028655    71010000

In [41]:
dfx['Y_FAIL'] = np.where(((dfx.P_FAIL <= .665541)), 0, 1)
print(pd.crosstab(dfx.Y_FAIL, dfx.FAILURE_TARGET, dropna=False))
pd.crosstab(dfx.Y_FAIL, dfx.FAILURE_TARGET).apply(lambda r: r/r.sum(), axis=1)

FAILURE_TARGET       0     1
Y_FAIL                      
0               149350  1565
1                11189  3102


FAILURE_TARGET        0        1
Y_FAIL                          
0               0.98963  0.01037
1               0.78294  0.21706

## 5.0 Summary and conclusions
* As you can see from these three scenarios, the best cut-off will depend greatly on the economics of your problem. Because of this, it is important to understand economic costs of both a false positive and a false negative. Just like most things in data science. The “best” answer depends on the context. If a false negative means a bolt will fly off and poke someone’s eye out, you have to make sure your model predictions reflect this hazard. Data science, like all things in this world, is subject to the context in which it is applied